In [1]:
import requests
import json
import time
import logging
import pandas as pd

# Konfigurasi Logging
logging.basicConfig(
    filename="leads_fetch.log",
    level=logging.INFO,
    format="%(asctime)s - %(levelname)s - %(message)s"
)

# Konfigurasi API
API_KEY = "eyJ0eXAiOiJKV1QiLCJhbGciOiJSUzI1NiIsImp0aSI6IjFkNmMyMWNjZDA5MWIyYTBmNTBmNTFkOGU1OTBjZmI5YTQ1MWM2OWU4OGI0YTRhYzlmNDI2M2IwN2I3NzI0ZjU4MWNjMDE4ZDQ2ODI4NWE4In0.eyJhdWQiOiJkZWE2YTVhYy0yNmFlLTRkNmMtYWM5NS1mNzNjOWVhMWRiZWIiLCJqdGkiOiIxZDZjMjFjY2QwOTFiMmEwZjUwZjUxZDhlNTkwY2ZiOWE0NTFjNjllODhiNGE0YWM5ZjQyNjNiMDdiNzcyNGY1ODFjYzAxOGQ0NjgyODVhOCIsImlhdCI6MTc0NTk4NDcwMSwibmJmIjoxNzQ1OTg0NzAxLCJleHAiOjE3NDg2NDk2MDAsInN1YiI6IjcxNjI2NzIiLCJncmFudF90eXBlIjoiIiwiYWNjb3VudF9pZCI6Mjk1ODIzMzUsImJhc2VfZG9tYWluIjoia29tbW8uY29tIiwidmVyc2lvbiI6Miwic2NvcGVzIjpbImNybSIsImZpbGVzIiwiZmlsZXNfZGVsZXRlIiwibm90aWZpY2F0aW9ucyIsInB1c2hfbm90aWZpY2F0aW9ucyJdLCJoYXNoX3V1aWQiOiI3NzU1NmM3NS05Nzc1LTQxZjYtODE2MS0xMzdjNWExMzkzMDciLCJhcGlfZG9tYWluIjoiYXBpLWcua29tbW8uY29tIn0.of9WJZZPS9wIXF-8AbUyfvTNKXadRnqZygsTFMQb2UkjqJuxuEh4c4UgdVTHvGnbtnqKpA4phBmsiSUEoDLhfyenYjbleT6bYJgUtNyUwaJfZftPJWPX3H5WX7k-HsicYLoIxrhwpSzLy3Z11vOfOsaQzYEv6Krf4CWQYYOe2xzmp9SkmQZmwGgeM6H7Z2grPz0GvGkLrljdXM9TGnCRJFB6MpM2X1cptNmdwyZbryEhymuDHexflPqMSjEp35mysrjWnRwvbHbUbIxWX6dAvRu_dnx3zxb2NQB8YNddwo7XtjgvCZtUTvLA4Cx7__Bw3CIfnpGfBCCFUa2zEFVGDg"
DOMAIN = "houseofomyogaschool.kommo.com"

# URL endpoint
LEADS_URL = f"https://{DOMAIN}/api/v4/leads"

# Headers untuk autentikasi
HEADERS = {
    "Authorization": f"Bearer {API_KEY}",
    "Content-Type": "application/json"
}

# Fungsi untuk mengambil data leads dengan paginasi
def get_leads():
    leads = []  # List untuk menyimpan semua leads
    page = 1  # Memulai dari halaman pertama
    max_retries = 3  # Maksimum jumlah percobaan ulang untuk permintaan
    retry_wait = 5  # Waktu tunggu antar percobaan dalam detik

    while True:
        logging.info(f"Fetching page {page}...")
        params = {"page": page}  # Parameter untuk paginasi
        retries = 0  # Inisialisasi jumlah percobaan

        while retries < max_retries:
            try:
                response = requests.get(LEADS_URL, headers=HEADERS, params=params, timeout=10)
                if response.status_code == 200:
                    data = response.json()
                    if "_embedded" in data and "leads" in data["_embedded"]:
                        leads.extend(data["_embedded"]["leads"])
                        logging.info(f"Page {page}: {len(data['_embedded']['leads'])} leads fetched.")
                    else:
                        logging.info("No more data found!")
                        return leads
                    # Cek apakah ada halaman berikutnya
                    if "_links" in data and "next" in data["_links"]:
                        page += 1
                    else:
                        logging.info("Reached the last page!")
                        return leads
                    break
                elif response.status_code == 429:  # Rate limit exceeded
                    logging.warning("Rate limit reached. Waiting for 10 seconds...")
                    time.sleep(10)  # Tunggu sebelum mencoba lagi
                else:
                    logging.error(f"Error: {response.status_code}, {response.text}")
                    return leads
            except requests.exceptions.RequestException as e:
                retries += 1
                logging.error(f"Request failed (attempt {retries}/{max_retries}): {e}")
                time.sleep(retry_wait)  # Tunggu sebelum mencoba ulang
        else:
            logging.error("Max retries reached. Stopping fetch process.")
            break
    return leads

# Fungsi untuk menyimpan data ke file JSON
def save_to_json(data, filename="leads_data.json"):
    try:
        with open(filename, "w") as file:
            json.dump(data, file, indent=4)
        logging.info(f"Data successfully saved to {filename}")
    except Exception as e:
        logging.error(f"Failed to save data to {filename}: {e}")

# Main program
if __name__ == "__main__":
    logging.info("Starting leads fetching process...")
    leads_data = get_leads()
    save_to_json(leads_data)
    print(f"Berhasil menarik {len(leads_data)} leads!")
    logging.info(f"Process completed. Total leads fetched: {len(leads_data)}.")

Berhasil menarik 28291 leads!


## **ambil semua kolom di leads**

In [2]:
import json

# Fungsi untuk mengekstrak custom fields ke dictionary yang lebih terstruktur
def extract_custom_fields(custom_fields):
    if not custom_fields:
        return {}
    extracted = {}
    for field in custom_fields:
        field_name = field.get('field_name', 'unknown_field')
        # Jika ada multiple values, ambil yang pertama
        values = field.get('values', [{}])[0].get('value', None)
        extracted[field_name] = values
    return extracted

# Fungsi untuk mengekstrak tags ke format string
def extract_tags(embedded):
    tags = embedded.get('tags', [])
    return ', '.join(tag['name'] for tag in tags)

# Fungsi utama untuk merapikan data leads
def clean_leads_data(leads_data):
    cleaned_data = []

    for lead in leads_data:
        # Data utama
        lead_data = {
            "id": lead.get("id"),
            "name": lead.get("name"),
            "price": lead.get("price"),
            "responsible_user_id": lead.get("responsible_user_id"),
            "status_id": lead.get("status_id"),
            "pipeline_id": lead.get("pipeline_id"),
            "created_at": lead.get("created_at"),
            "updated_at": lead.get("updated_at"),
        }

        # Tambahkan custom fields
        custom_fields = extract_custom_fields(lead.get("custom_fields_values", []))
        lead_data.update(custom_fields)

        # Tambahkan tags
        lead_data["tags"] = extract_tags(lead.get("_embedded", {}))

        cleaned_data.append(lead_data)

    return cleaned_data

# Baca data leads dari file JSON
with open("leads_data.json", "r") as file:
    leads_data = json.load(file)

# Bersihkan dan rapikan data
cleaned_data = clean_leads_data(leads_data)

# Konversi ke DataFrame untuk tampilan tabular
df = pd.DataFrame(cleaned_data)

print(f"Success")

Success


## **users**

In [3]:
# URL endpoint untuk mengambil data pengguna
USERS_URL = f"https://{DOMAIN}/api/v4/users"

# Headers untuk autentikasi
headers = {
    "Authorization": f"Bearer {API_KEY}",
    "Content-Type": "application/json"
}

# Ambil data pengguna
response = requests.get(USERS_URL, headers=headers)

if response.status_code == 200:
    try:
        users_data = response.json()["_embedded"]["users"]
        users_df = pd.DataFrame(users_data)

        # Bersihkan kolom nested jika ada
        if not users_df.empty and 'rights' in users_df.columns:
            rights_df = pd.json_normalize(users_df['rights'])
            users_df = pd.concat([users_df.drop(columns=['rights']), rights_df], axis=1)

        print("Success")
    except KeyError as e:
        print(f"Error: Struktur data tidak seperti yang diharapkan. {e}")
else:
    print(f"Error: {response.status_code}, {response.text}")

Success


## **pipeline**

In [4]:
# URL endpoint untuk mengambil data pipeline status
STATUS_URL = f"https://{DOMAIN}/api/v4/leads/pipelines"

# Headers untuk autentikasi
headers = {
    "Authorization": f"Bearer {API_KEY}",
    "Content-Type": "application/json"
}

# Ambil data pipeline status
response = requests.get(STATUS_URL, headers=headers)
if response.status_code == 200:
    pipelines_data = response.json()["_embedded"]["pipelines"]
    
    # Proses data untuk mendapatkan status_id dan nama status
    status_list = []
    for pipeline in pipelines_data:
        if "_embedded" in pipeline and "statuses" in pipeline["_embedded"]:
            for status in pipeline["_embedded"]["statuses"]:
                status_list.append({
                    "status_id": status["id"],
                    "status_name": status["name"],
                    "pipeline_id": pipeline["id"],
                    "pipeline_name": pipeline["name"]
                })
    
    # Buat DataFrame untuk status_id
    status_df = pd.DataFrame(status_list)
else:
    print(f"Error: {response.status_code}, {response.text}")

## **merge all data**

In [5]:
user_dict = dict(zip(users_df["id"], users_df["name"]))
df["responsible_user_id"] = df["responsible_user_id"].map(user_dict)

status_dict = dict(zip(status_df["status_id"], status_df["status_name"]))
df["status_id"] = df["status_id"].map(status_dict)

pipeline_dict = dict(zip(status_df["pipeline_id"], status_df["pipeline_name"]))
df["pipeline_id"] = df["pipeline_id"].map(pipeline_dict)

df.rename(columns={"responsible_user_id": "responsible_user_name"}, inplace=True)
df.rename(columns={"status_id": "status_name"}, inplace=True)
df.rename(columns={"pipeline_id": "pipeline_name"}, inplace=True)

## **timestamp**

In [6]:
df["created_at"] = pd.to_datetime(df["created_at"], unit="s")
df["updated_at"] = pd.to_datetime(df["updated_at"], unit="s")

## **export to xlsx**

In [7]:
import re

# Fungsi untuk membersihkan karakter ilegal
def remove_illegal_characters(value):
    if isinstance(value, str):  # Hanya untuk kolom dengan tipe string
        # Hapus karakter non-printable
        return re.sub(r"[\x00-\x1F\x7F-\x9F]", "", value)
    return value

# Terapkan fungsi ke semua kolom dalam DataFrame
df = df.applymap(remove_illegal_characters)
# df.to_excel("D:/House of Om/Sales/Kommo/fetch_kommo_data.xlsx", index=False)

C:\Users\user\AppData\Local\Temp\ipykernel_19380\3171005671.py:11: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df = df.applymap(remove_illegal_characters)


In [8]:
df

id                                               name  price  \
0      27935685  USD 400 / EUR 372 / IDR 6,400,000 - Invoice fo...      0   
1      27936751  2000USD Remaining Balance Twin Room - Invoice ...      0   
2      27938523  1920USD Remaining Balance Pelaga - Invoice for...      0   
3      27942237  USD1657 Remaining Balance Twin Room Pelaga - I...      0   
4      27922675  450USD Last Minute Price 300HR Online - Invoic...      0   
...         ...                                                ...    ...   
28286  31705079                                         younyeojin      0   
28287  31704761                                New lead from Tilda    400   
28288  31705555                                         younyeojin      0   
28289  31555313                    Lead from (Enkhjin Tseveendash)      0   
28290  31705369                           Lead from (@dkjnnnn__15)      0   

      responsible_user_name         status_name pipeline_name  \
0               House of OM  Successful payment  Sales funnel   
1               House of OM  Successful payment  Sales funnel   
2               House of OM  Successful payment  Sales funnel   
3               House of OM  Successful payment  Sales funnel   
4               House of OM  Successful payment  Sales funnel   
...                     ...                 ...           ...   
28286                Сергей           NEW LEADS  Sales funnel   
28287           House of OM  Successful payment  Sales funnel   
28288                Сергей           NEW LEADS  Sales funnel   
28289                 Tania             In work  Sales funnel   
28290                   Evy         UNQUALIFIED  Sales funnel   

               created_at          updated_at Payment amount IDR  \
0     2024-08-28 11:34:20 2024-09-30 11:26:17            6592000   
1     2024-08-28 12:43:57 2024-09-30 11:26:17           31930000   
2     2024-08-28 14:20:00 2024-09-30 11:26:17           30613248   
3     2024-08-28 17:37:15 2024-09-30 11:26:17           27478031   
4     2024-08-27 15:19:02 2024-09-30 11:26:18            7184250   
...                   ...                 ...                ...   
28286 2025-05-19 06:36:49 2025-05-19 08:06:27                NaN   
28287 2025-05-19 04:12:55 2025-05-19 08:13:35            6560000   
28288 2025-05-19 08:14:31 2025-05-19 08:14:33                NaN   
28289 2025-05-08 10:33:38 2025-05-19 08:15:33                NaN   
28290 2025-05-19 08:05:07 2025-05-19 08:16:54                NaN   

                 Pay way  ... o5_source o5_country o5_form name o5_location  \
0            CREDIT_CARD  ...       NaN        NaN          NaN         NaN   
1            CREDIT_CARD  ...       NaN        NaN          NaN         NaN   
2            CREDIT_CARD  ...       NaN        NaN          NaN         NaN   
3            CREDIT_CARD  ...       NaN        NaN          NaN         NaN   
4            CREDIT_CARD  ...       NaN        NaN          NaN         NaN   
...                  ...  ...       ...        ...          ...         ...   
28286                NaN  ...       NaN        NaN          NaN         NaN   
28287  Debit/Credit card  ...       NaN        NaN          NaN         NaN   
28288                NaN  ...       NaN        NaN          NaN         NaN   
28289                NaN  ...       NaN        NaN          NaN         NaN   
28290                NaN  ...       NaN        NaN          NaN         NaN   

      o5_Product Name o5_Payment type o5_Pay way o5_External_id o5_order_date  \
0                 NaN             NaN        NaN            NaN           NaN   
1                 NaN             NaN        NaN            NaN           NaN   
2                 NaN             NaN        NaN            NaN           NaN   
3                 NaN             NaN        NaN            NaN           NaN   
4                 NaN             NaN        NaN            NaN           NaN   
...               ...             ...        ...       

In [9]:
# Buang baris dengan status_name tertentu
excluded_statuses = ['CLIENTS', 'UNQUALIFIED']
df_leads = df[~df['status_name'].isin(excluded_statuses)].copy()

# Cek hasil
print("Jumlah leads setelah filter:", len(df_leads))
print(df_leads['status_name'].value_counts())

Jumlah leads setelah filter: 26251
status_name
NEW LEADS             19724
Successful payment     3922
In work                1742
Closed - won            534
Stage 1                 272
Closed - lost            56
Stage 2                   1
Name: count, dtype: int64


In [10]:
# # Pastikan kolom 'tags' bertipe string dulu (kalau ada NaN akan error pas .str)
# df_leads['tags'] = df_leads['tags'].astype(str)

# # Buat filter untuk kriteria 2
# filter_scholarship_free = (
#     (df_leads['status_name'] == 'NEW LEADS') &
#     (
#         df_leads['tags'].str.contains('Scholarship', case=False, na=False) |
#         df_leads['tags'].str.contains('Free Materials', case=False, na=False)
#     )
# )

# # Buang baris yang memenuhi kriteria tersebut
# df_leads = df_leads[~filter_scholarship_free].copy()

# # Cek hasil sementara
# print("Jumlah leads setelah kriteria 2:", len(df_leads))


In [11]:
# # Filter untuk kriteria 3
# filter_india_300 = (
#     (df_leads['status_name'] == 'NEW LEADS') &
#     (df_leads['tags'].str.contains('India_300', case=False, na=False))
# )

# # Drop baris yang cocok dengan kriteria ini
# df_leads = df_leads[~filter_india_300].copy()

# # Cek jumlah leads setelah kriteria 3
# print("Jumlah leads setelah kriteria 3:", len(df_leads))


In [12]:
# Pastikan kolom 'created_at' dalam format datetime
df_leads['created_at'] = pd.to_datetime(df_leads['created_at'], format='%m/%d/%Y %H:%M:%S', errors='coerce')

# Ambil tahun dari datetime
df_leads['created_year'] = df_leads['created_at'].dt.year

# Hitung jumlah leads per tahun
year_counts = df_leads['created_year'].value_counts().sort_index()

print("Jumlah leads per tahun:")
print(year_counts)


Jumlah leads per tahun:
created_year
2024     8157
2025    18094
Name: count, dtype: int64


In [13]:
df_leads

id                                               name  price  \
0      27935685  USD 400 / EUR 372 / IDR 6,400,000 - Invoice fo...      0   
1      27936751  2000USD Remaining Balance Twin Room - Invoice ...      0   
2      27938523  1920USD Remaining Balance Pelaga - Invoice for...      0   
3      27942237  USD1657 Remaining Balance Twin Room Pelaga - I...      0   
4      27922675  450USD Last Minute Price 300HR Online - Invoic...      0   
...         ...                                                ...    ...   
28284  31705249                                New lead from Tilda      0   
28286  31705079                                         younyeojin      0   
28287  31704761                                New lead from Tilda    400   
28288  31705555                                         younyeojin      0   
28289  31555313                    Lead from (Enkhjin Tseveendash)      0   

      responsible_user_name         status_name pipeline_name  \
0               House of OM  Successful payment  Sales funnel   
1               House of OM  Successful payment  Sales funnel   
2               House of OM  Successful payment  Sales funnel   
3               House of OM  Successful payment  Sales funnel   
4               House of OM  Successful payment  Sales funnel   
...                     ...                 ...           ...   
28284           House of OM           NEW LEADS  Sales funnel   
28286                Сергей           NEW LEADS  Sales funnel   
28287           House of OM  Successful payment  Sales funnel   
28288                Сергей           NEW LEADS  Sales funnel   
28289                 Tania             In work  Sales funnel   

               created_at          updated_at Payment amount IDR  \
0     2024-08-28 11:34:20 2024-09-30 11:26:17            6592000   
1     2024-08-28 12:43:57 2024-09-30 11:26:17           31930000   
2     2024-08-28 14:20:00 2024-09-30 11:26:17           30613248   
3     2024-08-28 17:37:15 2024-09-30 11:26:17           27478031   
4     2024-08-27 15:19:02 2024-09-30 11:26:18            7184250   
...                   ...                 ...                ...   
28284 2025-05-19 07:43:38 2025-05-19 07:43:41                NaN   
28286 2025-05-19 06:36:49 2025-05-19 08:06:27                NaN   
28287 2025-05-19 04:12:55 2025-05-19 08:13:35            6560000   
28288 2025-05-19 08:14:31 2025-05-19 08:14:33                NaN   
28289 2025-05-08 10:33:38 2025-05-19 08:15:33                NaN   

                 Pay way  ... o5_country o5_form name o5_location  \
0            CREDIT_CARD  ...        NaN          NaN         NaN   
1            CREDIT_CARD  ...        NaN          NaN         NaN   
2            CREDIT_CARD  ...        NaN          NaN         NaN   
3            CREDIT_CARD  ...        NaN          NaN         NaN   
4            CREDIT_CARD  ...        NaN          NaN         NaN   
...                  ...  ...        ...          ...         ...   
28284                NaN  ...        NaN          NaN         NaN   
28286                NaN  ...        NaN          NaN         NaN   
28287  Debit/Credit card  ...        NaN          NaN         NaN   
28288                NaN  ...        NaN          NaN         NaN   
28289                NaN  ...        NaN          NaN         NaN   

      o5_Product Name o5_Payment type o5_Pay way o5_External_id o5_order_date  \
0                 NaN             NaN        NaN            NaN           NaN   
1                 NaN             NaN        NaN            NaN           NaN   
2                 NaN             NaN        NaN            NaN           NaN   
3                 NaN             NaN        NaN            NaN           NaN   
4                 NaN             NaN        NaN            NaN           NaN   
...               ...             ...        ...            ...           ...   
28284             NaN             NaN        NaN            NaN           NaN   
28286        

In [14]:
# Pastikan kolom 'created_at' sudah dalam datetime (kalau belum)
df_leads['created_at'] = pd.to_datetime(df_leads['created_at'], format='%m/%d/%Y %H:%M:%S', errors='coerce')

# Ambil tahun dan bulan
df_leads['created_year'] = df_leads['created_at'].dt.year
df_leads['created_month'] = df_leads['created_at'].dt.month

# Hitung leads tahun 2024 mulai dari bulan Juli
leads_2024_july_onward = df_leads[(df_leads['created_year'] == 2024) & (df_leads['created_month'] >= 7)]

# Hitung juga untuk tahun 2025 penuh (kalau masih mau dibandingkan)
leads_2025 = df_leads[df_leads['created_year'] == 2025]

print("Jumlah leads dari Juli 2024 - Desember 2024:", len(leads_2024_july_onward))
print("Jumlah leads tahun 2025:", len(leads_2025))


Jumlah leads dari Juli 2024 - Desember 2024: 8108
Jumlah leads tahun 2025: 18094


In [15]:
leads_2025.to_excel(r"data\leads.xlsx")

In [16]:
# import requests
# from time import sleep
# from datetime import datetime

# ACCESS_TOKEN = "eyJ0eXAiOiJKV1QiLCJhbGciOiJSUzI1NiIsImp0aSI6IjA1N2I5YzQ3MDJiNWQ2NzM0NTQxYTBhN2NkNjdlYzI2Yzg2OTFlOTA4ODA3YmU5ZGZiMGNkOWY0MjI0NzllYWI1MDc1MTRlYTQ4MWVmOWE2In0.eyJhdWQiOiI1MWNkNTM1Zi1hZmE4LTRhYzgtODAwYS1jMzBlNWI0YjE4ZjAiLCJqdGkiOiIwNTdiOWM0NzAyYjVkNjczNDU0MWEwYTdjZDY3ZWMyNmM4NjkxZTkwODgwN2JlOWRmYjBjZDlmNDIyNDc5ZWFiNTA3NTE0ZWE0ODFlZjlhNiIsImlhdCI6MTc0NDYxMzM0MywibmJmIjoxNzQ0NjEzMzQzLCJleHAiOjE3NDU5NzEyMDAsInN1YiI6IjcxNjI2NzIiLCJncmFudF90eXBlIjoiIiwiYWNjb3VudF9pZCI6Mjk1ODIzMzUsImJhc2VfZG9tYWluIjoia29tbW8uY29tIiwidmVyc2lvbiI6Miwic2NvcGVzIjpbImNybSIsImZpbGVzIiwiZmlsZXNfZGVsZXRlIiwibm90aWZpY2F0aW9ucyIsInB1c2hfbm90aWZpY2F0aW9ucyJdLCJoYXNoX3V1aWQiOiJmNmU5NGYyZi0yMmE0LTQ1YzktODI4YS05OWMzNGIwMzA3YTQiLCJhcGlfZG9tYWluIjoiYXBpLWcua29tbW8uY29tIn0.U21vi8a9eDQeRHWImViFp4poG9kiG-RYWLPJ_5Iz442yDcTk-sXUiZWV0H2LEESLaGgcA4ZBzKS42AqMF3sMpY_3gSE2NFU3qkzc_j5D21DhwS_Yuz2KVS2i-lPD2eSQSsudmhcZ1jOPzkoCpFPREzugS6ItES530ku0x9WuoLj2V2MPxf6tir8ltqS30S4cgtqJV3i7dTnUEGfN0iSee2547Ie_OHCgTgnmsc1HiacKEswYcGf0LNrgyK-7u6OYDnFfcAyBj9jS381m3G2XgKeqYSZcUzl0fX_DZXA3V-jW3vMcy9_LIyZGiS14fxy10T92D1PXNV47X5iG1JE64g"
# headers = {
#     "Authorization": f"Bearer {ACCESS_TOKEN}"
# }

# params = {
#     "filter[type]": "incoming_chat"
# }

# url = "https://api-g.kommo.com/api/v4/notes"

# response = requests.get(url, headers=headers, params=params)

# if response.status_code == 200:
#     notes = response.json().get("_embedded", {}).get("notes", [])
    
#     print(f"✅ Total notes (chat masuk): {len(notes)}")
#     print("note_id, lead_id, created_by, created_at")

#     for note in notes:
#         note_id = note.get("id")
#         lead_id = note.get("entity_id")
#         created_by = note.get("created_by")
#         created_at = datetime.fromtimestamp(note["created_at"]).strftime("%Y-%m-%d %H:%M:%S")
#         print(f"{note_id}, {lead_id}, {created_by}, {created_at}")
# else:
#     print(f"❌ Gagal tarik notes: {response.status_code}")
#     print("Response:", response.text)
